In [1]:
import requests
import json
import pandas as pd
import numpy as np
from pandas.io.json import json_normalize
import os
import webbrowser
import folium
from folium import plugins

In [2]:
df = pd.read_excel("private_institute.xlsx")

In [75]:
df_code = pd.read_excel("district_code_seoul.xlsx")

In [76]:
df_code = df_code.rename(columns = {'통계청행정동코드' : 'code', '행자부행정동코드':'code_mois', '시도명':'city', '시군구명':'district', '행정동명': 'village'})
df_code = df_code.drop([0])
df_code["code"] = df_code["code"].astype('str')
df_code["code_district"] = df_code["code"].str[0:5]
df_code = df_code.drop_duplicates(['district'])
df_code = df_code.drop(['city','village', 'code', 'code_mois'], axis = 1)

In [68]:
df =df[['district', 'university related institute']]
df = df.drop([0])

df = pd.merge(df, df_code, how = "left")

KeyError: '[0] not found in axis'

In [94]:
df

district  university related institute code_district
0       종로구                            63         11010
1        중구                            38         11020
2       용산구                            67         11030
3       성동구                           152         11040
4       광진구                           241         11050
5      동대문구                           204         11060
6       중랑구                           173         11070
7       성북구                           274         11080
8       강북구                           141         11090
9       도봉구                           216         11100
10      노원구                           485         11110
11      은평구                           359         11120
12     서대문구                           204         11130
13      마포구                           257         11140
14      양천구                           721         11150
15      강서구                           422         11160
16      구로구                           226         11170
17      금천구                           121         11180
18     영등포구                           192         11190
19      동작구                           221         11200
20      관악구                           229         11210
21      서초구                           539         11220
22      강남구                          1153         11230
23      송파구                           651         11240
24      강동구                           421         11250

In [4]:
state_geo = 'TL_SCCO_EMD_WGS84.json'

In [98]:
m = folium.Map(location=[37.564214, 127.001699], tiles="OpenStreetMap", zoom_start=11)

In [99]:
m

In [96]:
m.choropleth(
    geo_data=state_geo,
    name='private institute',
    data=df,
    columns=['district', 'university related institute'],
    key_on='code_district',
    fill_color='Blues',
    fill_opacity=0.7,
    line_opacity=0.3,
    color = 'gray',
)

UnicodeDecodeError: 'cp949' codec can't decode byte 0xeb in position 411: illegal multibyte sequence

In [86]:
def center_calc(points_df):
    x = points_df.x
    y = points_df.y

    X = (max(x)+min(x))/2.
    Y = (max(y)+min(y))/2.

    return X, Y

def points_array(points):

    final_points = []

    for x in range(0, len(points)):

        if len(points[x]) == 2:
            final_points.append(points[x])
        else:
            target = points[x]
            for y in range(0, len(target)):
                final_points.append(target[y])

    return final_points

In [7]:
with open(state_geo, encoding='utf-8') as f:
    json_data = json.load(f)
print(json.dumps(json_data))  
#Error solution: jupyter notebook --NotebookApp.iopub_data_rate_limit=1.0e10
#json_data=open(state_geo).read()
#jsonResult = json.loads(json_data)

{"type": "FeatureCollection", "features": [{"type": "Feature", "geometry": {"type": "Polygon", "coordinates": [[[1020279.225626, 1987186.834294], [1020606.61792, 1987635.370114], [1020377.155579, 1987645.230254], [1020034.6237, 1987543.175949], [1020040.931096, 1987285.759382], [1020183.063147, 1987226.732693], [1020279.225626, 1987186.834294]]]}, "properties": {"EMD_CD": "42110101", "EMD_ENG_NM": "Bongui-dong", "EMD_KOR_NM": "\ubd09\uc758\ub3d9"}}, {"type": "Feature", "geometry": {"type": "Polygon", "coordinates": [[[1019844.71965, 1987019.754924], [1019859.590422, 1986911.845859], [1019954.409595, 1986806.091599], [1020031.190116, 1986765.722019], [1020183.063147, 1987226.732693], [1020040.931096, 1987285.759382], [1019844.71965, 1987019.754924]]]}, "properties": {"EMD_CD": "42110102", "EMD_ENG_NM": "Yoseon-dong", "EMD_KOR_NM": "\uc694\uc120\ub3d9"}}, {"type": "Feature", "geometry": {"type": "Polygon", "coordinates": [[[1019566.366263, 1986337.562046], [1019658.963215, 1986396.998144

In [87]:
center_locations = pd.DataFrame()
codes = []
names = []
x_list = []
y_list = []

for x in range(0, len(json_data['features'])):
    code = json_data['features'][x]['properties']['EMD_CD']
    name = json_data['features'][x]['properties']['EMD_KOR_NM']
    # 중앙값 생성
    points = json_data['features'][x]['geometry']['coordinates'][0]
    points = points_array(points)
    points_df = pd.DataFrame(points)
    points_df.columns = ['x','y']
    X, Y = center_calc(points_df)

    # 결과
    codes.append(code)
    names.append(name)
    x_list.append(X)
    y_list.append(Y)

# 데이터 프레임 생성
center_locations['CODE'] = codes
center_locations['NAME'] = names
center_locations['X'] = x_list
center_locations['Y'] = y_list

In [91]:
center_locations2 = center_locations[center_locations['Y'] >= 37.426026]
target_df = pd.merge(df,center_locations2, how = 'left')
target_df = target_df.dropna(axis=0, subset=['X','Y']) # 위치 정보 없는 값 제외

MergeError: No common columns to perform merge on. Merge options: left_on=None, right_on=None, left_index=False, right_index=False

In [ ]:
for i in range(0,len(target_df)):
    latitude = target_df.iloc[i]['Y']
    longitude = target_df.iloc[i]['X']
    location=(latitude, longitude)

    if target_df.iloc[i]['NAME'] in ['서초구','강남구'] :
        color = 'white'
    else:
        color = '#3186cc'

    folium.CircleMarker(location, radius=10,color=color,fill_color=color,fill_opacity = 0.1, opacity=0.0,  popup=target_df.iloc[i]['NAME'] + "\n" + str(int(round(target_df.iloc[i]['VALUE']/10000,0))) + "만원").add_to(m)


folium.LayerControl(collapsed=False).add_to(m)